# Assignment 3: Building Neural Networks and CNN
## Bonus Question 


# ACADEMIC INTERGITY STATEMENT 


I/We certify that the code and data in this assignment were generated independently, 
using only the tools and resources defined in the course and that I/We did not receive any external help, coaching or contributions during the production of this work.


In [25]:
# Step 1: Import required libraries
import pandas as pd
import numpy as np
import math
import matplotlib.pyplot as plt

In [26]:
# Step 2: Read, preprocess and print main statistic about the dataset
df = pd.read_csv('penguins.csv')

In [27]:
df.dropna(inplace=True)

In [28]:
# Step 3: Convert features with string datatype to categorical(species, island, sex)
#df['year'] = df['year'].astype('category')
df['species'] = df.species.astype('category')
df['island'] = df.island.astype('category')
df['sex'] = df.sex.astype('category')

print(df.dtypes)

species              category
island               category
bill_length_mm        float64
bill_depth_mm         float64
flipper_length_mm     float64
body_mass_g           float64
sex                  category
year                    int64
dtype: object


In [29]:
# Step 4: Normalize non-categorical features (bill_length_mm, bill_depth_mm, flipper_length_mm, body_mass_g)

only_category = df.select_dtypes('category').columns
only_numerical = df.select_dtypes([float,int]).columns
temp_df = pd.DataFrame()

def min_max_normalize(column):
    return (column - column.min()) / (column.max() - column.min())

for column in only_numerical:
    temp_df[column] = min_max_normalize(df[column])

for colummn in only_category:
    one_hot = pd.get_dummies(df[colummn])                
    unique_values = df[colummn].unique()
    for values in unique_values[1:]:        
        temp_df = temp_df.join(one_hot[values])

df = temp_df
df.head

<bound method NDFrame.head of      bill_length_mm  bill_depth_mm  flipper_length_mm  body_mass_g  year  \
0          0.254545       0.666667           0.152542     0.291667   0.0   
1          0.269091       0.511905           0.237288     0.305556   0.0   
2          0.298182       0.583333           0.389831     0.152778   0.0   
4          0.167273       0.738095           0.355932     0.208333   0.0   
5          0.261818       0.892857           0.305085     0.263889   0.0   
..              ...            ...                ...          ...   ...   
339        0.861818       0.797619           0.593220     0.361111   1.0   
340        0.414545       0.595238           0.508475     0.194444   1.0   
341        0.636364       0.607143           0.355932     0.298611   1.0   
342        0.680000       0.702381           0.644068     0.388889   1.0   
343        0.658182       0.666667           0.440678     0.298611   1.0   

     Gentoo  Chinstrap  Biscoe  Dream  female  
0        

In [30]:
# Step 5: Choose your target Y - We will be using a binary classifier to predict which gender a penguin belongs to (female or male). In this case, the column 'sex' 
# can be used as Y(target)

# Step 6: Create the data matrices for X (input) and Y (target) in a shape X = Nxd and Y = Nx1, where N is a number of data samples and d is a number of features

df = df.sample(frac=1) # shuffles data to avoid bias or variance

Y = (df['female'].to_numpy())
print(Y.shape)

df_x = df.drop(columns=['female'])


X = df_x.to_numpy()

X.shape




(333,)


(333, 9)

In [31]:
# Step 7: Divide the dataset into training and test, as 80% training, 20% testing dataset. 

s_f = 0.8 # splitting factor
s_i = math.floor(s_f * X.shape[0]) # splitting index
X_train = X[:s_i]
Y_train = Y[:s_i]
X_test = X[s_i:]
Y_test = Y[s_i:]

# Step 8: Print the shape of you X_train, Y_train, X_test and Y_test. 
print(X_train.shape)
print(X_test.shape)
print(Y_train.shape)
print(Y_test.shape)



(266, 9)
(67, 9)
(266,)
(67,)


In [32]:
class Perceptron:
    def __init__(self, iterations=10000, learning_rate=1e-2):
        '''
        '''
        self.iterations = iterations
        self.learning_rate = learning_rate
        self.weights = 0

    def sigmoid(self, x):
        '''
        '''
        return 1 / (1 + np.exp(-x))

    def mse_loss(self, y, y_pred):
        '''
        '''
        return 0.5 * np.power((y - y_pred), 2)
    
    def fit(self, X, Y):
        '''
        '''
        x_shape = np.shape(X)[1]
        y_shape = np.shape(Y)[0]
        self.W = np.random.uniform(0, 1, size=x_shape)
        self.w0 = 0
        for i in range(self.iterations):
            linear_output = X.dot(self.W) + self.w0
            y_pred = self.sigmoid(linear_output)
            error_gradient = self.mse_loss(Y, y_pred) * self.sigmoid(linear_output)
            grad_wrt_w = X.T.dot(error_gradient)
            grad_wrt_w0 = np.sum(error_gradient)
            self.W = self.W  - (self.learning_rate * grad_wrt_w)
            self.w0 = self.w0 - (self.learning_rate  * grad_wrt_w0)
            #print(self.W, self.w0)
        
    def predict(self, x):
        output = np.dot(x, self.W.T) + self.w0
        y_predicted = self.sigmoid(output)
        lst = []
        for i in y_predicted:
            if i > 0.5:
                value = 1
            else:
                value = 0
            lst.append(value)
        return lst
    
    def accuracy(self, y_actual, y_predicted):
        '''
        '''
        accruaracy = np.sum(y_actual == y_predicted)/ y_actual.shape[0]
        return accruaracy * 100        

In [33]:
per = Perceptron()
per.fit(X_train, Y_train)
predictions = per.predict(X_test)

print('The accuracy of Perceptron is :', per.accuracy(Y_test, predictions))


The accuracy of Perceptron is : 52.23880597014925


In [34]:
class LogitRegression():
    learning_rate = None
    iterations = None
    bias = None
    total_loss = []
    summed_weights = None

    def __init__(self, learning_rate = 1e-6, iterations=100000):
        # Takes as an input hyperparameters: learning rate and the
        '''
        '''
        self.learning_rate = learning_rate
        self.iterations = iterations
       
    def sigmoid(self, input_exponent):
        '''
        '''
        denom = 1 + np.exp(-input_exponent)
        return 1/denom
    
    def cost(self, y_predicted, y_actual):
        '''
        '''
        cost_value = (1/y_actual.shape[0]) * np.sum((- y_actual * np.log(y_predicted)) - ((1 - y_actual) * np.log(1 - y_predicted)))
        return abs(cost_value)

    def gradient_descent(self, pred, X, y_actual):
        ''''
        '''
        delta = pred - y_actual
        grad_descent_value = np.dot(X.T, delta) / y_actual.shape[0]
        return grad_descent_value

    def predict(self,X):
        X = np.array(X)
        self.bias = np.ones((X.shape[0],1))
        X = np.hstack([self.bias, X])
        pred_prob = self.sigmoid(np.dot(X, self.summed_weights))
        pred = (pred_prob >= 0.5) * 1
        return pred
        

    def temp_predict(self, weights, X):
        '''
        '''
        #weights_T = np.transpose(weights)
        weights_T = weights
        weights_x = np.dot(X, weights_T)
        predicted_value = self.sigmoid(weights_x)
        return predicted_value

    def fit(self, X, Y):
        '''
        '''
        # X = np.array(X)
        # Y = np.array(Y)
        #weights = np.random.uniform(0, 1, size=X.shape[1])
        self.bias = np.ones((X.shape[0],1))
        X = np.hstack([self.bias, X])
        weights = np.random.uniform(0, 1, size=X.shape[1])
        self.summed_weights = weights
        for indx in range(self.iterations):
            predicted_value = self.temp_predict(self.summed_weights, X) 
            # print("pred value shape in loop", predicted_value.shape)            #(266, 266)
            cost = self.cost(predicted_value, Y)
            self.total_loss.append(cost)    
            # print("Cost value", cost)        
            grad_descent_value = self.gradient_descent(predicted_value, X, Y)
            # print("Final weights sjahe", self.summed_weights.shape) #(8,)
            # print("GRad shape", grad_descent_value.shape)            #(8, 266)
            self.summed_weights = self.summed_weights - (self.learning_rate * grad_descent_value)

            print("Loss Values: ", cost)
    
    def get_accuracy(self, y_actual, y_predicated):
        '''
        '''
        accruaracy = np.sum(y_actual == y_predicated)/ y_actual.shape[0]
        return accruaracy * 100
    
    def get_final_weights(self):
        print(self.summed_weights)

    def loss_graph(self):
        '''
        '''
        plt.plot(range(100000), self.total_loss, color='black')
        plt.xlabel("Iterations Value")
        plt.ylabel("Loss Value")
        plt.show()
        
    

In [35]:
log = LogitRegression(learning_rate = 1e-2)
log.fit(X_train, Y_train)
y_pred_fin = log.predict(X_test)
print("Accuracy", log.get_accuracy(Y_test, y_pred_fin))

Loss Values:  19.56219860066331
Loss Values:  19.737312581295622
Loss Values:  19.913306617232866
Loss Values:  20.090176798971527
Loss Values:  20.26791907145238
Loss Values:  20.44652923391917
Loss Values:  20.62600293983382
Loss Values:  20.80633569684876
Loss Values:  20.987522866837043
Loss Values:  21.169559665980813
Loss Values:  21.35244116491849
Loss Values:  21.536162288951296
Loss Values:  21.720717818309442
Loss Values:  21.906102388478427
Loss Values:  22.092310490585714
Loss Values:  22.279336471848037
Loss Values:  22.46717453607978
Loss Values:  22.655818744262294
Loss Values:  22.845263015174602
Loss Values:  23.03550112608534
Loss Values:  23.226526713506207
Loss Values:  23.41833327400665
Loss Values:  23.610914165090012
Loss Values:  23.804262606130738
Loss Values:  23.998371679372735
Loss Values:  24.19323433098853
Loss Values:  24.388843372198963
Loss Values:  24.585191480453137
Loss Values:  24.782271200668283
Loss Values:  24.98007494652901
Loss Values:  25.1785

# References

1) https://towardsdatascience.com/what-is-a-perceptron-basics-of-neural-networks-c4cfea20c590 <br>
2) https://www.sciencedirect.com/topics/computer-science/logistic-regression#:~:text=Logistic%20regression%20is%20a%20process,%2Fno%2C%20and%20so%20on. <br>
3) https://numpy.org/ <br>
4) https://pandas.pydata.org/docs/reference/api/pandas.get_dummies.html <br>